In [38]:
class SchoolPerson:
    
    schoolpopulation = 0
    
    def __init__(self, name, age ):
        self.name = name
        self.age = age
       
        
        SchoolPerson.schoolpopulation +=1 
        print(f'Initialized person:{self.name}')
        
    
    def tellName(self):
        print(f'Name: {self.name} , age: {self.age}')
    
    @classmethod
    def Count(cls):
        print('number of people:', cls.schoolpopulation)

    
class SchoolTeacher(SchoolPerson):
    def __init__(self, name, age, salary):
        SchoolPerson.__init__(self, name ,age)
        self.salary = salary
        
    def tellName(self):
        print(f'Name: {self.name} , age: {self.age}, salary: {self.salary}')
        super().tellName()
        
    @classmethod
    def Count(cls):
        super().Count()


In [39]:
c = SchoolPerson('Nazim', 30)
c.name
d = SchoolPerson('Rasim', 23)



Initialized person:Nazim
Initialized person:Rasim


In [40]:
SchoolPerson.Count()

number of people: 2


In [41]:
f = SchoolTeacher('John', 35, 1111)


Initialized person:John


In [42]:
SchoolTeacher.Count()

number of people: 3


In [11]:
c.__dict__

{'name': 'Nazim', 'age': 30}

In [56]:
x = 23

class Addition:
    
    x = 10
    
    def __init__(self, x):
        self.x = x
        
    def addY_1(self, y):
        print('Result:', self.x + y)
    
    @classmethod
    def addY_2(cls, y):
        print('Result:', cls.x + y)
        
    @staticmethod
    def addY_3(y):
        print('Result:', x  + y)
    
    

In [57]:
n = Addition(23)

In [58]:
n.addY_1(2)

Result: 25


In [61]:
# n.addY_2(2)

n.addY_3(2)

Result: 25


In [55]:
t = Addition(30)
t.addY_1(2)
t.addY_2(2)
Addition.addY_2(2)

Result: 32
Result: 12
Result: 12


In [9]:
def buterbrod(icfunksiya):
    def corekle():
        print('/------- \\')
        icfunksiya()
        print('\-------//')
    return corekle()



  
@buterbrod
def pendirli():
    print('=========')

/------- \
\-------//


In [2]:
from itertools import count
class Asset:
    """Generic class for producing/consuming assets. Specific asset classes can
    inherit from this class.

    Parameters:
    -----------
    max_power     : int/float
        Maximum asset power in MW electric
    min_power     : int/float
        Minimium asset load in MW electric

    Usage:
    ------
    Use the set_load and get_load methods to set and get asset status in MW.

    Convention is negative values for inputs (consumption) and positive
    values for outputs (production).
    """

    _freq_to_multiplier = {"H": 1, "15T": (1 / 4), "1T": (1 / 60)}
    _ids = count(0)

    def __init__(self, name, max_power, min_power):
        if min_power > max_power:
            raise ValueError("'min_power' can not be larger than 'max_power'.")

        self.name = name
        self.id = next(self._ids)
        self.max_power = max_power
        self.min_power = min_power
        self.modes = {"max": max_power, "min": min_power}

    def __repr__(self):
        return f"{self.__class__.__name__}(self, max_power={self.max_power}, min_power={self.min_power})"

    def set_load(self, load):
        """Set Asset load in MW.

        Convention is negative value for consumption and positive value
        for production. Subclasses might use a different convention if
        this seems more intiutive.

        Returns the load that is set in MW.
        """
        if load < self.min_power or load > self.max_power:
            warnings.warn(
                f"Chosen Asset load for {self.name} is out of range. "
                f"Should be between {self.min_power} and {self.max_power}. "
                f"Function will return boundary load level for now."
            )
            load = min(max(load, self.min_power), self.max_power)
        return load

    def set_mode(self, mode):
        """ """
        load = self.modes[mode]
        return self.set_load(load)

    def MW_to_MWh(self, MW):
        """Performs conversion from MW to MWh using the time_factor variable."""
        return MW * self.time_factor

    def MWh_to_MW(self, MWh):
        """Performs conversion from MWh to MW using the time_factor variable."""
        return MWh / self.time_factor

    def set_freq(self, freq):
        """
        Function that aligns time frequency between Model and Asset.
        Can be '1T', '15T' or 'H'
        The time_factor variable is used in subclasses to perform MW to MWh conversions.
        """
        self.freq = freq
        self.time_factor = Asset._freq_to_multiplier[freq]

    def set_financials(self, capex, opex, devex, lifetime=None, depreciate=True, salvage_value=0):
        """Set financial data of the asset."""
        self.capex = capex
        self.opex = opex
        self.devex = devex
        self.lifetime = lifetime
        self.depreciate = depreciate
        self.salvage_value = salvage_value

In [3]:
class WaterStorage(Asset):
    
    def __init__(
        self, 
        name,
        max_power,
        min_power,
        roundtrip_eff,
        lifetime,
        power_capex, 
        energy_capex,
        opex,
        heat_demand = 23.5*1.06,
        heat_st_capacity = 70, 
        storage_size = 22650
    ):
        super().__init__(name, max_power, min_power)
        self.rt_eff = roundtrip_eff
        self.lifetime = lifetime
        self.power_capex = power_capex #Euro/kW
        self.energy_capex = energy_capex  #Euro/kWh
        self.opex = opex
        self.heat_demand = heat_demand #MW
        self.heat_st_cap = heat_st_cap #kWh/m3
        self.storage_size= storage_size #m3
        
    def __repr__(self):
        return (
            # f"{self.__class__.__name__}(name={self.name}, max_power={self.max_power}, "
            # f"min_power={self.min_power}, efficiency={self.efficiency})"
            f"""{self.__class__.__name__}(name={self.name}, max_power={self.max_power}, 
            min_power={self.min_power}, efficiency={self.efficiency})"""
        )
    
    def set_capacity(self, capacity):
        if not isinstance(capacity, (int, float)):
            raise TypeError('Should be float')
        if capacity < 0:
            raise ValueError('Capacity has to be positive')
        self.capacity = capacity
            
    def cost_function(self):
        return self.heat_demand * self.power_capex * 1e6 + self.heat_st_cap * self.storage_size * self.energy_capex
        
    
    
        

In [10]:
s = WaterStorage


In [89]:
c.__dict__

{'name': 'WaterStorage',
 'id': 3,
 'max_power': 350,
 'min_power': 122,
 'modes': {'max': 300, 'min': 122},
 'freq': '1T',
 'time_factor': 0.016666666666666666}

In [84]:
d = Asset('Pump', 200, 20)

In [85]:
d.__dict__

{'name': 'Pump',
 'id': 1,
 'max_power': 200,
 'min_power': 20,
 'modes': {'max': 200, 'min': 20}}

In [96]:
class Eboiler(Asset):
    """Subclass for an E-boiler."""

    def __init__(self, name, max_power, min_power=0, efficiency=0.99):
        super().__init__(name, min_power=-max_power, max_power=-min_power)
        self.efficiency = efficiency
        self.max_thermal_output = max_power * 0.99

    def __repr__(self):
        return (
            f"{self.__class__.__name__}(name={self.name}, max_power={self.max_power}, "
            f"min_power={self.min_power}, efficiency={self.efficiency})"
        )

    def set_load(self, load):
        """Set load in MWe, returns (load, heat_output) in MWe and MWth

        Convention is negative numbers for consumption.
        Inserting a positive value will return an exception.
        """

        if load > 0:
            raise ValueError(
                f"Eboiler.set_load() only accepts negative numbers by convention. "
                f"{load} was inserted."
            )

        load = super().set_load(load)
        heat_output = -load * self.efficiency
        return (load, heat_output)

    def set_heat_output(self, heat_output):
        """Set heat output in MWth, returns tuple (heat_output, eload) in MW"""
        load = -heat_output / self.efficiency
        load, heat_output = self.set_load(load)
        return heat_output, load

In [91]:
e = Eboiler('eboyul', 300)

In [97]:
e.__dict__

{'name': 'eboyul',
 'id': 4,
 'max_power': 0,
 'min_power': -300,
 'modes': {'max': 0, 'min': -300},
 'efficiency': 0.99,
 'max_thermal_output': 297.0}

In [98]:
e.set_financials(300,400,500)

In [99]:
e.__dict__

{'name': 'eboyul',
 'id': 4,
 'max_power': 0,
 'min_power': -300,
 'modes': {'max': 0, 'min': -300},
 'efficiency': 0.99,
 'max_thermal_output': 297.0,
 'capex': 300,
 'opex': 400,
 'devex': 500,
 'lifetime': None,
 'depreciate': True,
 'salvage_value': 0}